<a href="https://colab.research.google.com/github/dominikjanyga/network-analysis/blob/main/network_analysis_data_collection.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

# 1. Loading libraries
The first step is to import the libraries that will be helpful in scraping the data and later to analyze it.

In [2]:
import pandas as pd
import networkx as nx
import matplotlib.pyplot as plt
import seaborn as sns
import numpy as np
import yfinance as yf

In [ ]:
from google.colab import drive

drive.mount('/content/drive')

Drive already mounted at /content/drive; to attempt to forcibly remount, call drive.mount("/content/drive", force_remount=True).


#2. Stooq data
Next, we are using a function that reads the HTML table from the stooq webpage. The goal is to obtain all ticker symbols for the companies that are listed on the Warsaw Stock Exchange.  

In [5]:
ticker_list = []

for page in range(1, 9):
    page_url = f"https://stooq.pl/q/i/?s=wig&l={page}"
    wig_table = pd.read_html(page_url)[1]
    wig_selected_rows = wig_table.iloc[5:-1, 0].tolist()
    ticker_list.extend(wig_selected_rows)

print(ticker_list)
len(ticker_list)

['06N', '11B', '1AT', '3RG', 'AAT', 'ABE', 'ABS', 'ACG', 'ACP', 'ACT', 'AGO', 'AGT', 'ALE', 'ALI', 'ALL', 'ALR', 'AMB', 'AMC', 'ANR', 'APE', 'APN', 'APR', 'APT', 'ARH', 'ART', 'ASB', 'ASE', 'AST', 'ATC', 'ATD', 'ATG', 'ATP', 'ATR', 'ATS', 'ATT', 'AWM', 'B24', 'BBD', 'BBT', 'BCM', 'BCS', 'BCX', 'BDX', 'BDZ', 'BFT', 'BHW', 'BIO', 'BIP', 'BLO', 'BMC', 'BMX', 'BNP', 'BOS', 'BOW', 'BRS', 'CAP', 'CAR', 'CAV', 'CBF', 'CCC', 'CDL', 'CDR', 'CEZ', 'CIG', 'CLC', 'CLD', 'CLE', 'CLN', 'CMP', 'COG', 'CPL', 'CPR', 'CPS', 'CRI', 'CRJ', 'CRM', 'CSR', 'CTX', 'DAD', 'DAT', 'DBE', 'DCR', 'DEK', 'DEL', 'DGA', 'DGE', 'DIG', 'DNP', 'DOM', 'DVL', 'EAH', 'EAT', 'ECH', 'EHG', 'EKP', 'ELT', 'ENA', 'ENE', 'ENI', 'ENT', 'EQU', 'ERB', 'ERG', 'ETL', 'EUR', 'FAB', 'FEE', 'FMG', 'FON', 'FRO', 'FSG', 'FTE', 'GEA', 'GIF', 'GKI', 'GMT', 'GOP', 'GPP', 'GPW', 'GRN', 'GRX', 'GTC', 'GTN', 'HDR', 'HEL', 'HRP', 'HUG', 'ICE', 'IFI', 'IIA', 'IMC', 'IMS', 'INC', 'ING', 'INK', 'INL', 'INP', 'IPE', 'IPO', 'ITB', 'IZO', 'IZS', 'JRH'

320

In [6]:
tickers = [ticker + ".WA" for ticker in ticker_list]

We use yfinance to search for the company details such as: sector, industry,companyOfficers, shortName, longName etc.

In [3]:
yf.Ticker('ALL.WA').info

{'address1': 'al. Jana Pawla II 43b',
 'address2': 'Budynek Podium Park',
 'city': 'Kraków',
 'zip': '31-864',
 'country': 'Poland',
 'phone': '48 12 252 3400',
 'fax': '48 12 252 3401',
 'website': 'https://ailleron.com/pl',
 'industry': 'Software - Infrastructure',
 'industryKey': 'software-infrastructure',
 'industryDisp': 'Software - Infrastructure',
 'sector': 'Technology',
 'sectorKey': 'technology',
 'sectorDisp': 'Technology',
 'longBusinessSummary': 'Ailleron S.A. provides technological services and IT solutions worldwide. The company offers retail banking solutions, including omnichannel retail banking platform that provides value added modules, and internet and mobile banking platform; and corporate and business banking platform, which offers desktop channel and mobile access solutions. It also provides leasing solutions, such as LeaseTech Offer Manager, LeaseTech Customer Platform, Lease Commerce, LeaseTech Virtual Branch, and LeaseTech Front Office; LiveBank, a communicati

In [8]:
company_data = []
officers_data = []

for ticker in tickers:
    stock = yf.Ticker(ticker)
    info = stock.info
    sector = info.get('sector', 'No data')
    industry = info.get('industry', 'No data')
    name = info.get('longName', 'No data')
    short_name = info.get('shortName', 'No data')
    roe = info.get('returnOnEquity', 'No data')
    roa = info.get('returnOnAssets', 'No data')
    p_to_book = info.get('priceToBook', 'No data')
    debt_to_eq = info.get('debtToEquity', 'No data')
    beta = info.get('beta', 'No data')
    companyOfficers = info.get('companyOfficers', 'No data')

    # Append the data to the company_data list
    company_data.append({
        'longName': name,
        'shortName': short_name,
        'ticker': ticker,
        'sector': sector,
        'industry': industry,
        'returnOnEquity': roe,
        'p_to_book': p_to_book,
        'debt_to_eq': debt_to_eq,
        'beta': beta

    })

    officers_data.append({
        'longName': name,
        'shortName': short_name,
        'ticker': ticker,
        'companyOfficers': companyOfficers
    })

company_data
officers_data
#for data in company_data:
#   print(f"Ticker: {data['ticker']}, Sector: {data['sector']}, Industry: {data['industry']}")


[{'longName': 'Magna Polonia S.A.',
  'shortName': '06MAGNA',
  'ticker': '06N.WA',
  'companyOfficers': [{'maxAge': 1,
    'name': 'Mr. Miroslaw  Janisiewicz',
    'age': 46,
    'title': 'President of the Management Board',
    'yearBorn': 1977,
    'exercisedValue': 0,
    'unexercisedValue': 0}]},
 {'longName': '11 bit studios S.A.',
  'shortName': '11BIT',
  'ticker': '11B.WA',
  'companyOfficers': [{'maxAge': 1,
    'name': 'Mr. Przemyslaw Piotr Marszal',
    'title': 'President of the Management Board',
    'fiscalYear': 2023,
    'totalPay': 730660,
    'exercisedValue': 0,
    'unexercisedValue': 0},
   {'maxAge': 1,
    'name': 'Mr. Grzegorz  Miechowski',
    'title': 'Member of Management Board',
    'fiscalYear': 2023,
    'totalPay': 731688,
    'exercisedValue': 0,
    'unexercisedValue': 0},
   {'maxAge': 1,
    'name': 'Mr. Michal Wojciech Drozdowski',
    'title': 'Member of the Management Board',
    'fiscalYear': 2023,
    'totalPay': 723584,
    'exercisedValue': 0,

#3. Financial data


In [ ]:
urls = []
for company in ticker_list:
  url = f'https://stooq.pl/q/h/?s={company}'
  urls.append(url)

['https://stooq.pl/q/h/?s=06N',
 'https://stooq.pl/q/h/?s=11B',
 'https://stooq.pl/q/h/?s=1AT',
 'https://stooq.pl/q/h/?s=3RG',
 'https://stooq.pl/q/h/?s=AAT',
 'https://stooq.pl/q/h/?s=ABE',
 'https://stooq.pl/q/h/?s=ABS',
 'https://stooq.pl/q/h/?s=ACG',
 'https://stooq.pl/q/h/?s=ACP',
 'https://stooq.pl/q/h/?s=ACT',
 'https://stooq.pl/q/h/?s=AGO',
 'https://stooq.pl/q/h/?s=AGT',
 'https://stooq.pl/q/h/?s=ALE',
 'https://stooq.pl/q/h/?s=ALI',
 'https://stooq.pl/q/h/?s=ALL',
 'https://stooq.pl/q/h/?s=ALR',
 'https://stooq.pl/q/h/?s=AMB',
 'https://stooq.pl/q/h/?s=AMC',
 'https://stooq.pl/q/h/?s=ANR',
 'https://stooq.pl/q/h/?s=APE',
 'https://stooq.pl/q/h/?s=APN',
 'https://stooq.pl/q/h/?s=APR',
 'https://stooq.pl/q/h/?s=APT',
 'https://stooq.pl/q/h/?s=ARH',
 'https://stooq.pl/q/h/?s=ART',
 'https://stooq.pl/q/h/?s=ASB',
 'https://stooq.pl/q/h/?s=ASE',
 'https://stooq.pl/q/h/?s=AST',
 'https://stooq.pl/q/h/?s=ATC',
 'https://stooq.pl/q/h/?s=ATD',
 'https://stooq.pl/q/h/?s=ATG',
 'https:

In [ ]:
wig_tables = []
for index, url in enumerate(urls):
  table = pd.read_html(url)[1].copy()
  ticker_symbol = ticker_list[index]
  table['ticker'] = ticker_symbol
  wig_tables.append(table)
wig_tables

[                                                   Lp  \
 0                                                 NaN   
 1                                                 NaN   
 2                                                 NaN   
 3                                                 NaN   
 4                                                 NaN   
 5                                                   1   
 6                                               Razem   
 7                        · Cena nominalna akcji: 1.00   
 8                                · Free Float: 75.54%   
 9         · Liczba wszystkich akcji: 13,921,975 akcji   
 10           · Akcje uprzywilejowane co do głosu: nie   
 11  document.write(Modernizr.svg?'<svg xmlns="http...   
 
                                          Akcjonariusz Udział w kapitale  \
 0                                                 NaN               NaN   
 1   Ulubione GPW, WIG20, Akcje Indeksy, Azja, Euro...               NaN   
 2              

In [ ]:
final_wig_table = pd.concat(wig_tables, ignore_index=True)

In [ ]:
final_wig_table['Lp'] = pd.to_numeric(final_wig_table['Lp'], errors='coerce')

In [ ]:
final_wig_table = final_wig_table.dropna(subset=['Lp'])

In [ ]:
final_wig_table.to_csv("/content/drive/MyDrive/Projects/network-analysis/shareholder_data_15102024", index=False)

In [ ]:
csv_file_path = '/content/drive/MyDrive/Projects/network-analysis/shareholder_data_15102024'
data = pd.read_csv(csv_file_path)
data

Lp               Akcjonariusz Udział w kapitale  Liczba akcji  \
0     1.0      RG Ventures Sp. z o.o            24.46%     3405807.0   
1     1.0        Grzegorz Miechowski             6.97%      168413.0   
2     2.0            TFI Esaliens SA             6.51%      157257.0   
3     3.0  OFE Nationale-Nederlanden             5.69%      137648.0   
4     4.0         Przemysław Marszał             4.96%      120003.0   
...   ...                        ...               ...           ...   
3655  3.0               OFE Generali             6.35%     1461659.0   
3656  4.0                     ZUE SA             1.15%      264652.0   
3657  5.0         TFI BNP Paribas SA             0.77%      177171.0   
3658  6.0                    DFE PKO             0.22%       49763.0   
3659  7.0                 TFI PKO SA             0.16%       37294.0   

      Ostatnia zmiana Wartość rynkowa (PLN) Udział na WZA  Liczba głosów  \
0                 0.0              10.4 mln        24.46%      3405807.0   
1                 0.0              47.4 mln         6.97%       168413.0   
2            -13027.0              44.3 mln         6.51%       157257.0   
3                 0.0              38.8 mln         5.69%       137648.0   
4                 0.0              33.8 mln         4.96%       120003.0   
...               ...                   ...           ...            ...   
3655              0.0              13.2 mln         6.35%      1461659.0   
3656              0.0              2.39 mln         0.00%            0.0   
3657         117040.0              1.60 mln         0.77%       177171.0   
3658          22184.0               450 tys         0.22%        49763.0   
3659              0.0               337 tys         0.16%        37294.0   

      Ostatnia zmiana.1 Data aktualizacji ticker  
0                   0.0       26 wrz 2024    06N  
1                   0.0       27 sie 2024    11B  
2              -13027.0       28 cze 2024    11B  
3                   0.0       29 gru 2023    11B  
4                   0.0        6 cze 2024    11B  
...                 ...               ...    ...  
3655                0.0        7 cze 2024    ZUE  
3656                0.0       28 cze 2017    ZUE  
3657           117040.0       28 cze 2024    ZUE  
3658            22184.0       29 gru 2023    ZUE  
3659                0.0       28 cze 2024    ZUE  

[3660 rows x 11 columns]

In [ ]:
#new_table = tabele_razem[tabele_razem['Lp'].str.isnumeric()]

# Convert the "Lp" column to numeric, coerce non-numeric values to NaN
tabele_razem['Lp'] = pd.to_numeric(tabele_razem['Lp'], errors='coerce')

# Filter the DataFrame based on numerical values in the "Lp" column
new_table = tabele_razem.dropna(subset=['Lp'])

In [ ]:
#new_table.to_csv("WIG.csv")

#excel_file_path = '/content/drive/MyDrive/Colab Notebooks/wig_dane/wig_dane_full.xlsx'
csv_path = '/content/drive/MyDrive/Projects/GPW_network_analysis/WIG_table.csv'

# Save the DataFrame to CSV in Google Drive
new_table.to_csv(csv_path, index=False)

In [ ]:
stock_data_path = '/content/drive/MyDrive/Projects/GPW_network_analysis/WIG_table.csv'
stock_data = pd.read_csv(stock_data_path)
stock_data

Lp               Akcjonariusz Udział w kapitale  Liczba akcji  \
0     1.0      RG Ventures Sp. z o.o            24.46%     3405807.0   
1     1.0      TFI Allianz Polska SA             9.51%      229878.0   
2     2.0        Grzegorz Miechowski             6.97%      168413.0   
3     3.0  OFE Nationale-Nederlanden             5.99%      144900.0   
4     4.0            TFI Esaliens SA             5.74%      138671.0   
...   ...                        ...               ...           ...   
3583  1.0                   Fram FIZ            33.65%     2188592.0   
3584  2.0         Stanisław Pargieła            11.42%      742800.0   
3585  3.0           Andrzej Pargieła            10.60%      689423.0   
3586  4.0            Artur Mączyński             9.79%      636896.0   
3587  5.0            Lech Pasturczak             7.81%      507896.0   

      Ostatnia zmiana Wartość rynkowa (PLN) Udział na WZA  Liczba głosów  \
0                 0.0              12.7 mln        24.46%      3405807.0   
1                 0.0               126 mln         9.51%       229878.0   
2                 0.0              92.6 mln         6.97%       168413.0   
3                 0.0              79.7 mln         5.99%       144900.0   
4               332.0              76.3 mln         5.74%       138671.0   
...               ...                   ...           ...            ...   
3583              0.0              5.95 mln        33.65%      2188592.0   
3584              0.0              2.02 mln        11.42%       742800.0   
3585              0.0              1.88 mln        10.60%       689423.0   
3586              0.0              1.73 mln         9.79%       636896.0   
3587              0.0              1.38 mln         7.81%       507896.0   

      Ostatnia zmiana.1 Data aktualizacji ticker  
0                   0.0       24 lis 2023    06N  
1                   0.0       17 lis 2023    11B  
2                   0.0       17 lis 2023    11B  
3                   0.0       17 lis 2023    11B  
4                 332.0       29 wrz 2023    11B  
...                 ...               ...    ...  
3583                0.0       29 lis 2023    ZUK  
3584                0.0       29 lis 2023    ZUK  
3585                0.0       29 lis 2023    ZUK  
3586                0.0       29 lis 2023    ZUK  
3587                0.0       29 lis 2023    ZUK  

[3588 rows x 11 columns]

In [ ]:
SEKTORY = ["WIG_BANKI",
"WIG_BUDOW",
"WIG_CHEMIA",
"WIG_ENERG",
"WIG_GORNIC",
"WIG_GRY",
"WIG_INFO",
"WIG_LEKI",
"WIG_MEDIA",
"WIG_MOTO",
"WIG_NRCHOM",
"WIG_ODZIEZ",
"WIG_PALIWA",
"WIG_SPOZYW"]

In [ ]:
SECTORS_TICKERS = []

for i in SEKTORY:
  url_sectors = f"https://stooq.pl/q/i/?s={i}"
  SECTORS_TICKERS.append(url_sectors.lower())

SECTORS_TICKERS

['https://stooq.pl/q/i/?s=wig_banki',
 'https://stooq.pl/q/i/?s=wig_budow',
 'https://stooq.pl/q/i/?s=wig_chemia',
 'https://stooq.pl/q/i/?s=wig_energ',
 'https://stooq.pl/q/i/?s=wig_gornic',
 'https://stooq.pl/q/i/?s=wig_gry',
 'https://stooq.pl/q/i/?s=wig_info',
 'https://stooq.pl/q/i/?s=wig_leki',
 'https://stooq.pl/q/i/?s=wig_media',
 'https://stooq.pl/q/i/?s=wig_moto',
 'https://stooq.pl/q/i/?s=wig_nrchom',
 'https://stooq.pl/q/i/?s=wig_odziez',
 'https://stooq.pl/q/i/?s=wig_paliwa',
 'https://stooq.pl/q/i/?s=wig_spozyw']

In [ ]:
wig_table_sectors = []
for i, url in enumerate(SECTORS_TICKERS):
  tables_sectors = pd.read_html(url)[1]
  tables_sectors.columns = tables_sectors.columns.droplevel(0)
  tables_sectors.reset_index(drop=True, inplace = True)
  table_sectors = tables_sectors.copy()
  sector_name = SEKTORY[i] #wig_banki
  table_sectors.loc[:, 'sectors'] = sector_name  #table['company'] = ticker
  wig_table_sectors.append(table_sectors)

In [ ]:
wig_table_sectors_together = pd.concat(wig_table_sectors)
wig_table_sectors_together = wig_table_sectors_together.dropna(subset=['Symbol'])
wig_table_sectors_together

Symbol       Nazwa     Kurs  \
5                                                 ALR       ALIOR   73.960   
6                                                 BHW    HANDLOWY  101.000   
7                                                 BNP      BNPPPL   81.400   
8                                                 BOS         BOS   10.940   
9                                                 GTN       GETIN    0.606   
..                                                ...         ...      ...   
18                                                PPS      PEPEES    1.210   
19                                                SEK        SEKO   11.400   
20                                                TAR  TARCZYNSKI   49.500   
21                                                WWL       WAWEL  750.000   
22  document.write(Modernizr.svg?'<svg xmlns="http...         NaN      NaN   

    Zmiana   Data  Kapitalizacja (mln)  Wartość księgowa (mln)  \
5   +1.32%  10:42              9653.20                 8584.27   
6   -1.75%  10:44             13197.00                 9019.48   
7   -1.69%  10:41             12080.00                13130.93   
8   +0.55%  10:39              1016.80                 2120.18   
9   +0.17%  10:39               115.00                  103.35   
..     ...    ...                  ...                     ...   
18   0.00%   9:00               114.95                  179.05   
19  -1.72%   9:44                75.81                   83.99   
20   0.00%  2 sty               561.67                  475.67   
21   0.00%  10:29              1124.80                  670.01   
22     NaN    NaN                  NaN                     NaN   

    Zysk na akcję (ttm)  C/Z (ttm)  C/WK  Stopa dyw. (%)     sectors  
5               13.7736       5.37  1.13             NaN   WIG_BANKI  
6               17.4237       5.80  1.46             8.8   WIG_BANKI  
7               11.1892       7.31  0.92             NaN   WIG_BANKI  
8                0.9802      11.16  0.48             NaN   WIG_BANKI  
9                   NaN        NaN  1.11           261.2   WIG_BANKI  
..                  ...        ...   ...             ...         ...  
18               0.0818      14.79  0.64             8.2  WIG_SPOZYW  
19               2.2308       5.11  0.90             2.8  WIG_SPOZYW  
20               5.9639       8.30  1.18             4.4  WIG_SPOZYW  
21              43.1034      17.40  1.68             1.1  WIG_SPOZYW  
22                  NaN        NaN   NaN             NaN  WIG_SPOZYW  

[215 rows x 12 columns]

In [ ]:
#excel_file_path = '/content/drive/MyDrive/Colab Notebooks/wig_dane/wig_dane_full.xlsx'
new_csv_path = '/content/drive/MyDrive/Projects/GPW_network_analysis/wig_table_sectors_together.csv'

# Save the DataFrame to CSV in Google Drive
wig_table_sectors_together.to_csv(new_csv_path, index=False)

In [ ]:
#stock_data = pd.read_csv('stock_data.csv')
#wig_table_sectors_together = pd.read_csv('wig_table_sectors_together.csv')
merged_data = pd.merge(stock_data, wig_table_sectors_together[['Symbol', 'sectors']], left_on='ticker', right_on='Symbol', how='left')
merged_data = merged_data.drop(columns=['Symbol'])
merged_data
#merged_data.to_csv('merged_stock_data.csv', index=False)

Lp               Akcjonariusz Udział w kapitale  Liczba akcji  \
0     1.0      RG Ventures Sp. z o.o            24.46%     3405807.0   
1     1.0      TFI Allianz Polska SA             9.51%      229878.0   
2     2.0        Grzegorz Miechowski             6.97%      168413.0   
3     3.0  OFE Nationale-Nederlanden             5.99%      144900.0   
4     4.0            TFI Esaliens SA             5.74%      138671.0   
...   ...                        ...               ...           ...   
3583  1.0                   Fram FIZ            33.65%     2188592.0   
3584  2.0         Stanisław Pargieła            11.42%      742800.0   
3585  3.0           Andrzej Pargieła            10.60%      689423.0   
3586  4.0            Artur Mączyński             9.79%      636896.0   
3587  5.0            Lech Pasturczak             7.81%      507896.0   

      Ostatnia zmiana Wartość rynkowa (PLN) Udział na WZA  Liczba głosów  \
0                 0.0              12.7 mln        24.46%      3405807.0   
1                 0.0               126 mln         9.51%       229878.0   
2                 0.0              92.6 mln         6.97%       168413.0   
3                 0.0              79.7 mln         5.99%       144900.0   
4               332.0              76.3 mln         5.74%       138671.0   
...               ...                   ...           ...            ...   
3583              0.0              5.95 mln        33.65%      2188592.0   
3584              0.0              2.02 mln        11.42%       742800.0   
3585              0.0              1.88 mln        10.60%       689423.0   
3586              0.0              1.73 mln         9.79%       636896.0   
3587              0.0              1.38 mln         7.81%       507896.0   

      Ostatnia zmiana.1 Data aktualizacji ticker  sectors  
0                   0.0       24 lis 2023    06N      NaN  
1                   0.0       17 lis 2023    11B  WIG_GRY  
2                   0.0       17 lis 2023    11B  WIG_GRY  
3                   0.0       17 lis 2023    11B  WIG_GRY  
4                 332.0       29 wrz 2023    11B  WIG_GRY  
...                 ...               ...    ...      ...  
3583                0.0       29 lis 2023    ZUK      NaN  
3584                0.0       29 lis 2023    ZUK      NaN  
3585                0.0       29 lis 2023    ZUK      NaN  
3586                0.0       29 lis 2023    ZUK      NaN  
3587                0.0       29 lis 2023    ZUK      NaN  

[3588 rows x 12 columns]

In [ ]:
merged_data_sorted = merged_data.sort_values(by='ticker')
filtered_data = merged_data_sorted[merged_data_sorted['sectors'].isna()]
print(filtered_data)


        Lp               Akcjonariusz Udział w kapitale  Liczba akcji  \
0      1.0      RG Ventures Sp. z o.o            24.46%     3405807.0   
77    25.0         TFI BNP Paribas SA             0.01%        1049.0   
76    24.0  DFE Nationale-Nederlanden             0.04%        5997.0   
75    23.0               TFI Alior SA             0.05%        8400.0   
74    22.0        TFI Credit Agricole             0.08%       12330.0   
...    ...                        ...               ...           ...   
3583   1.0                   Fram FIZ            33.65%     2188592.0   
3584   2.0         Stanisław Pargieła            11.42%      742800.0   
3585   3.0           Andrzej Pargieła            10.60%      689423.0   
3586   4.0            Artur Mączyński             9.79%      636896.0   
3587   5.0            Lech Pasturczak             7.81%      507896.0   

      Ostatnia zmiana Wartość rynkowa (PLN) Udział na WZA  Liczba głosów  \
0                 0.0              12.7 mln    

In [ ]:
unique_tickers = filtered_data['ticker'].drop_duplicates()
unique_tickers

0       06N
77      ABE
137     ACT
140     ADV
192     ALE
       ... 
3541    XTB
3549    XTP
3565    ZMT
3574    ZRE
3583    ZUK
Name: ticker, Length: 131, dtype: object

In [ ]:
G = nx.from_pandas_edgelist(stock_data, 'ticker', 'Akcjonariusz', edge_attr=True)

In [ ]:
edgelist = nx.to_edgelist(G)
edgelist

EdgeDataView([('06N', 'RG Ventures Sp. z o.o', {'Lp': 1.0, 'Udział w kapitale': '24.46%', 'Liczba akcji': 3405807.0, 'Ostatnia zmiana': 0.0, 'Wartość rynkowa (PLN)': '12.7 mln', 'Udział na WZA': '24.46%', 'Liczba głosów': 3405807.0, 'Ostatnia zmiana.1': 0.0, 'Data aktualizacji': '24 lis 2023'}), ('11B', 'TFI Allianz Polska SA', {'Lp': 1.0, 'Udział w kapitale': '9.51%', 'Liczba akcji': 229878.0, 'Ostatnia zmiana': 0.0, 'Wartość rynkowa (PLN)': '126 mln', 'Udział na WZA': '9.51%', 'Liczba głosów': 229878.0, 'Ostatnia zmiana.1': 0.0, 'Data aktualizacji': '17 lis 2023'}), ('11B', 'Grzegorz Miechowski', {'Lp': 2.0, 'Udział w kapitale': '6.97%', 'Liczba akcji': 168413.0, 'Ostatnia zmiana': 0.0, 'Wartość rynkowa (PLN)': '92.6 mln', 'Udział na WZA': '6.97%', 'Liczba głosów': 168413.0, 'Ostatnia zmiana.1': 0.0, 'Data aktualizacji': '17 lis 2023'}), ('11B', 'OFE Nationale-Nederlanden', {'Lp': 3.0, 'Udział w kapitale': '5.99%', 'Liczba akcji': 144900.0, 'Ostatnia zmiana': 0.0, 'Wartość rynkowa (P

In [ ]:
plt.figure(figsize=(35, 25))
min_value=0.1
nx.draw_kamada_kawai(G, with_labels=False,
        node_color = ['red' if node in stock_data['Akcjonariusz'].values else 'blue' for node in G],
        node_size = [v * 30 for v in dict(G.degree()).values()],
        width=[max(v[2]['Udział w kapitale']/1000000000000, min_value) for v in edgelist],
        edgecolors='#696969')
plt.show()

TypeError: unsupported operand type(s) for /: 'str' and 'int'

<Figure size 3500x2500 with 0 Axes>

In [ ]:
stock = yf.Ticker('ALE.WA')

In [ ]:
info = stock.info
sector = info.get('sector', 'No data available')
industry = info.get('industry', 'No data available')
sector


'Consumer Cyclical'

In [ ]:
info

{'address1': '1, rue Hildegard von Bingen',
 'city': 'Luxembourg',
 'zip': '1282',
 'country': 'Luxembourg',
 'phone': '352 2 6495 84370',
 'website': 'https://www.allegro.eu',
 'industry': 'Internet Retail',
 'industryKey': 'internet-retail',
 'industryDisp': 'Internet Retail',
 'sector': 'Consumer Cyclical',
 'sectorKey': 'consumer-cyclical',
 'sectorDisp': 'Consumer Cyclical',
 'longBusinessSummary': 'Allegro.eu S.A. operates a go-to commerce platform for consumers in Poland and internationally. It operates through Allegro, Ceneo, Mall, and Allegro International segments. The company operates allegro.pl, an e-commerce marketplace that sells products in various categories, including automotive; home and garden; books, media, collectibles, and art; fashion and shoes; electronics; kids; health and beauty; sports and leisure; and supermarket. It also operates ceneo.pl, a multi-category price comparison site; Mall Group, an e-commerce platform; and eBilet, an event ticket sales site faci